# Curacao Risk Level for Extreme Sea Level Hazard Using Gornitz et al. (1994)
# Curacao Multi-Criteria Risk Level for Extreme Sea Level Hazard Using Mclaughlin and Cooper (2010)


In [81]:
import pandas as pd
import geopandas as gpd
import matplotlib.pyplot as plt
from shapely.geometry import Point, Polygon
from scipy.spatial import KDTree
import numpy as np

# Additional imports
import pystac_client
import xarray as xr
import pathlib
import os
import geopandas as gpd
import matplotlib as mpl
from matplotlib import colors
import rasterio

import cartopy.crs as ccrs
import cartopy
import plotly.graph_objects as go
import plotly.express as px
from rasterio.plot import show

import matplotlib.colors as mcolors
from shapely.geometry import Point
import pandas as pd

from tqdm import tqdm

import webbrowser
from pathlib import Path
import os
import time

from itertools import compress
import pandas as pd

import matplotlib.pyplot as plt
import cartopy.crs as ccrs
import cartopy
import plotly.graph_objects as go
import plotly.express as px
import plotly.io as pio

from tqdm import tqdm

from shapely.geometry import box



In [82]:
Exposure_df=pd.read_csv(r"P:\11209197-018-global-coastal-atlas\MSc_students\ClenmarRowe\Data\Processed_data_CVI_components\Exposure\Caribbean_Exposure_classified.csv")
# Exposure_df["Sediment_Type - Exposure level"]=Exposure_df["Sediment Type"]


Exposure_df

transect_id country_id      continent        country_name  \
0       BOX_116_353_2        COL  South America            Colombia   
1       BOX_116_353_3        COL  South America            Colombia   
2       BOX_116_353_4        COL  South America            Colombia   
3       BOX_116_353_5        COL  South America            Colombia   
4       BOX_116_353_6        COL  South America            Colombia   
...               ...        ...            ...                 ...   
37504  BOX_139_002_61        DOM  North America  Dominican Republic   
37505  BOX_139_002_62        DOM  North America  Dominican Republic   
37506  BOX_139_002_63        DOM  North America  Dominican Republic   
37507  BOX_139_002_64        DOM  North America  Dominican Republic   
37508  BOX_139_002_65        DOM  North America  Dominican Republic   

       Percentage of Built Up Area  LECZ Area÷LECZ mean elevation  \
0                              0.0                   1.366501e+06   
1                              0.0                   1.974146e+06   
2                              0.0                   3.834474e+06   
3                              0.0                   5.239073e+06   
4                              0.0                   6.112962e+06   
...                            ...                            ...   
37504                          0.0                   1.793014e+06   
37505                          0.0                   1.861771e+06   
37506                          0.0                   1.970466e+06   
37507                          0.0                   2.126400e+06   
37508                          0.0                   2.078267e+06   

       Neashore Slope (tanβ or m^-1)  Population Within 1km of the coastline  \
0                          11.291917                                     0.0   
1                          13.060951                                     0.0   
2                          13.060951                                     0.0   
3                          11.420912                                     0.0   
4                          11.420912                                     0.0   
...                              ...                                     ...   
37504                       3.867398                                  1593.0   
37505                       3.867398                                  2227.0   
37506                       3.790441                                  2710.0   
37507                       3.790441                                  2617.0   
37508                       4.570359                                  1775.0   

       Sediment Type                                   geometry  \
0                4.0        POINT (-71.8798045985 12.250683718)   
1                2.0    POINT (-71.87698143850001 12.247308305)   
2                4.0       POINT (-71.8756318462 12.2431443263)   
3                2.0       POINT (-71.8752334021 12.2387721729)   
4                2.0       POINT (-71.8748349513 12.2343999454)   
...              ...                                        ...   
37504            4.0       POINT (-71.6681862112 17.9652589019)   
37505            4.0       POINT (-71.6662284163 17.9614175026)   
37506            4.0        POINT (-71.664582619 17.9574419454)   
37507            4.0  POINT (-71.6629367897 17.953466310899998)   
37508            4.0  POINT (-71.6612909283 17.949490598900002)   

       Percentage of Built Up Area - Exposure level  \
0                                                 1   
1                                                 1   
2                                                 1   
3                                                 1   
4                                                 1   
...                                             ...   
37504                                             1   
37505                                             1   
37506                                             1   
37507       

In [83]:
Vulnerability_df=pd.read_csv(r"P:\11209197-018-global-coastal-atlas\MSc_students\ClenmarRowe\Data\Processed_data_CVI_components\Vulnerability\Caribbean_Vulnerability_classified.csv")

Vulnerability_df

transect_id country_id      continent        country_name  \
0       BOX_116_353_2        COL  South America            Colombia   
1       BOX_116_353_3        COL  South America            Colombia   
2       BOX_116_353_4        COL  South America            Colombia   
3       BOX_116_353_5        COL  South America            Colombia   
4       BOX_116_353_6        COL  South America            Colombia   
...               ...        ...            ...                 ...   
37504  BOX_139_002_61        DOM  North America  Dominican Republic   
37505  BOX_139_002_62        DOM  North America  Dominican Republic   
37506  BOX_139_002_63        DOM  North America  Dominican Republic   
37507  BOX_139_002_64        DOM  North America  Dominican Republic   
37508  BOX_139_002_65        DOM  North America  Dominican Republic   

       Infant Mortality Rate (3_yr_Average)  GDP per Capita (3_yr_Average)  \
0                                 11.433333                    5974.501814   
1                                 11.433333                    5974.501814   
2                                 11.433333                    5974.501814   
3                                 11.433333                    5974.501814   
4                                 11.433333                    5974.501814   
...                                     ...                            ...   
37504                             27.800000                    7939.336437   
37505                             27.800000                    7939.336437   
37506                             27.800000                    7939.336437   
37507                             27.800000                    7939.336437   
37508                             27.800000                    7939.336437   

       Mean Years of Schooling  Deaths from Recent Shocks (2004-2023)  \
0                     8.862860                                   3143   
1                     8.862860                                   3143   
2                     8.862860                                   3143   
3                     8.862860                                   3143   
4                     8.862860                                   3143   
...                        ...                                    ...   
37504                 9.306864                                   1370   
37505                 9.306864                                   1370   
37506                 9.306864                                   1370   
37507                 9.306864                                   1370   
37508                 9.306864                                   1370   

       World Protected Areas (Status and Governance)  \
0                                                  3   
1                                                  3   
2                                                  3   
3                                                  3   
4                                                  3   
...                                              ...   
37504                                              5   
37505                                              5   
37506                                              5   
37507                                              5   
37508                                              5   

                                        geometry  \
0            POINT (-71.8798045985 12.250683718)   
1        POINT (-71.87698143850001 12.247308305)   
2           POINT (-71.8756318462 12.2431443263)   
3           POINT (-71.8752334021 12.2387721729)   
4           POINT (-71.8748349513 12.2343999454)   
...                                          ...   
37504       POINT (-71.6681862112 17.9652589019)   
37505       POINT (-71.6662284163 17.9614175026)   
37506        POINT (-71.664582619 17.9574419454)   
37507  POINT (-71.6629367897 17.953466310899998)   
37508  POINT (-71.6612909283 17.949490598900002)   

       Infant Mortality Rate (3_yr_Average) -

In [84]:
Hazard_df=pd.read_csv(r"P:\11209197-018-global-coastal-atlas\MSc_students\ClenmarRowe\Data\Processed_data_CVI_components\Hazard\Present\Caribbean_Hazards_classified.csv")
Hazard_df

transect_id country_id      continent        country_name  \
0       BOX_116_353_2        COL  South America            Colombia   
1       BOX_116_353_3        COL  South America            Colombia   
2       BOX_116_353_4        COL  South America            Colombia   
3       BOX_116_353_5        COL  South America            Colombia   
4       BOX_116_353_6        COL  South America            Colombia   
...               ...        ...            ...                 ...   
37504  BOX_139_002_61        DOM  North America  Dominican Republic   
37505  BOX_139_002_62        DOM  North America  Dominican Republic   
37506  BOX_139_002_63        DOM  North America  Dominican Republic   
37507  BOX_139_002_64        DOM  North America  Dominican Republic   
37508  BOX_139_002_65        DOM  North America  Dominican Republic   

       ESL_100yrRP  EWH_100yrRP  Land_Subsidence_2010  \
0         0.946771     4.455543                   NaN   
1         0.946771     4.455543                   NaN   
2         0.946771     4.455543                   NaN   
3         0.946771     4.455543                   NaN   
4         0.946771     4.455543                   NaN   
...            ...          ...                   ...   
37504     1.246410    22.563481                   2.0   
37505     1.246410    22.563481                   2.0   
37506     1.246410    22.563481                   2.0   
37507     1.246410    22.563481                   2.0   
37508     1.246410    22.563481                   2.0   

       Shoreline_Change_Rate_PC                                   geometry  \
0                    -16.441771        POINT (-71.8798045985 12.250683718)   
1                      0.335379    POINT (-71.87698143850001 12.247308305)   
2                      1.878836       POINT (-71.8756318462 12.2431443263)   
3                      0.490707       POINT (-71.8752334021 12.2387721729)   
4                     -0.052123       POINT (-71.8748349513 12.2343999454)   
...                         ...                                        ...   
37504                  0.288753       POINT (-71.6681862112 17.9652589019)   
37505                  0.166001       POINT (-71.6662284163 17.9614175026)   
37506                  0.092415        POINT (-71.664582619 17.9574419454)   
37507                 -0.027472  POINT (-71.6629367897 17.953466310899998)   
37508                 -0.094827  POINT (-71.6612909283 17.949490598900002)   

       ESL_100yrRP - Hazard level  EWH_100yrRP - Hazard level  \
0                             1.0                           1   
1                             1.0                           1   
2                             1.0                           1   
3                             1.0                           1   
4                             1.0                           1   
...                           ...                         ...   
37504                         2.0                           4   
37505                         2.0                           4   
37506                         2.0                           4   
37507                         2.0                           4   
37508                         2.0                           4   

       Land_Subsidence_2010 - Hazard level  \
0                                      NaN   
1                                      NaN   
2                                      NaN   
3                                      NaN   
4                                      NaN   
...                                    ...   
37504                                  2.0   
37505                                  2.0   
37506                                  2.0   
37507                                  2.0   
37508                                  2.0   

       Shoreline_Change_Rate_PC - Hazard level  
0                                          5.0  
1                                          2.0  
2                                          1.0  
3    

Curacao Risk Level for Extreme Sea Level Hazard Using Gornitz et al. (1994) CVI6 

In [85]:
save_directory=r"P:\11209197-018-global-coastal-atlas\MSc_students\ClenmarRowe\Data\Processed_data_CVI_components\Risk\01 Present\Caribbean\Haz_Exp_Vul"
img_directory_path=r"P:\11209197-018-global-coastal-atlas\MSc_students\ClenmarRowe\Data\Processed_data_CVI_components\Caribbean Plots\Risk_Level_PC"
os.makedirs(img_directory_path, exist_ok=True)

Discrete_Risk_Bins= True
Both_Plots=True

In [86]:
# UNCOMMENT AS NEEDED

gornitz_hazard_used=Hazard_df.columns[-1]  #Toggle as needed between -4 and -1



Value_to_show=title_name=gornitz_hazard_used.replace(" - Hazard level","")


title_name=gornitz_hazard_used.replace(" - Hazard level","")

gornitz_ESL=pd.concat([Hazard_df.iloc[:,0],Hazard_df[gornitz_hazard_used],Exposure_df.iloc[:,-5:],Vulnerability_df.iloc[:,-5:]],axis=1)
gornitz_ESL

transect_id  Shoreline_Change_Rate_PC - Hazard level  \
0       BOX_116_353_2                                      5.0   
1       BOX_116_353_3                                      2.0   
2       BOX_116_353_4                                      1.0   
3       BOX_116_353_5                                      2.0   
4       BOX_116_353_6                                      2.0   
...               ...                                      ...   
37504  BOX_139_002_61                                      2.0   
37505  BOX_139_002_62                                      2.0   
37506  BOX_139_002_63                                      2.0   
37507  BOX_139_002_64                                      2.0   
37508  BOX_139_002_65                                      2.0   

       Percentage of Built Up Area - Exposure level  \
0                                                 1   
1                                                 1   
2                                                 1   
3                                                 1   
4                                                 1   
...                                             ...   
37504                                             1   
37505                                             1   
37506                                             1   
37507                                             1   
37508                                             1   

       LECZ Area÷LECZ mean elevation - Exposure level  \
0                                                   2   
1                                                   3   
2                                                   4   
3                                                   4   
4                                                   5   
...                                               ...   
37504                                               2   
37505                                               2   
37506                                               3   
37507                                               3   
37508                                               3   

       Neashore Slope (tanβ or m^-1) - Exposure level  \
0                                                 4.0   
1                                                 4.0   
2                                                 4.0   
3                                                 4.0   
4                                                 4.0   
...                                               ...   
37504                                             3.0   
37505                                             3.0   
37506                                             3.0   
37507                                             3.0   
37508                                             3.0   

       Population Within 1km of the coastline - Exposure level  \
0                                                      1         
1                                                      1         
2                                                      1         
3                                                      1         
4                                                      1         
...                                                  ...         
37504                                                  2         
37505                                                  2         
37506                                                  2         
37507                                                  2         
37508                                                  2         

       Sediment Type - Exposure level  \
0                                 4.0   
1                                 2.0   
2                                 4.0   
3                                 2.0   
4                                 2.0   
...                               ...   
37504                             4.0   
37505                             4.0   
37506                   

In [87]:
# Define Hazard units to show on plot

if "ESL" in gornitz_hazard_used:
    units="m"
if "EWH" in gornitz_hazard_used:
    units="m"
if "Change_rate" in gornitz_hazard_used:
    units="m/yr"
if "Land" in gornitz_hazard_used:
    units=""

Haz_Component= Hazard_df[Value_to_show].apply(lambda x: f"{Value_to_show} {x:.2f}{units}")

In [88]:
indicator_num=len(gornitz_ESL.columns)-1
indicator_num

11

In [89]:
if indicator_num>9:
    var=" (Haz_Exp_Vul)"
else:
    var=" (Haz_Exp)"

In [90]:
gornitz_ESL_filled=gornitz_ESL.copy()
gornitz_ESL_filled["Risk Level"]=(gornitz_ESL[gornitz_hazard_used]+(np.nansum(gornitz_ESL.iloc[:,2:7],axis=1)/len(gornitz_ESL.iloc[:,2:7]))+(np.nansum(gornitz_ESL.iloc[:,-5:],axis=1)/len(gornitz_ESL.iloc[0,-5:])))/3
# gornitz_ESL_filled["Risk Level Class"] = np.round(gornitz_ESL_filled["Risk Level"])
gornitz_ESL_filled["Risk Level Class"] = np.nan
gornitz_ESL_filled

transect_id  Shoreline_Change_Rate_PC - Hazard level  \
0       BOX_116_353_2                                      5.0   
1       BOX_116_353_3                                      2.0   
2       BOX_116_353_4                                      1.0   
3       BOX_116_353_5                                      2.0   
4       BOX_116_353_6                                      2.0   
...               ...                                      ...   
37504  BOX_139_002_61                                      2.0   
37505  BOX_139_002_62                                      2.0   
37506  BOX_139_002_63                                      2.0   
37507  BOX_139_002_64                                      2.0   
37508  BOX_139_002_65                                      2.0   

       Percentage of Built Up Area - Exposure level  \
0                                                 1   
1                                                 1   
2                                                 1   
3                                                 1   
4                                                 1   
...                                             ...   
37504                                             1   
37505                                             1   
37506                                             1   
37507                                             1   
37508                                             1   

       LECZ Area÷LECZ mean elevation - Exposure level  \
0                                                   2   
1                                                   3   
2                                                   4   
3                                                   4   
4                                                   5   
...                                               ...   
37504                                               2   
37505                                               2   
37506                                               3   
37507                                               3   
37508                                               3   

       Neashore Slope (tanβ or m^-1) - Exposure level  \
0                                                 4.0   
1                                                 4.0   
2                                                 4.0   
3                                                 4.0   
4                                                 4.0   
...                                               ...   
37504                                             3.0   
37505                                             3.0   
37506                                             3.0   
37507                                             3.0   
37508                                             3.0   

       Population Within 1km of the coastline - Exposure level  \
0                                                      1         
1                                                      1         
2                                                      1         
3                                                      1         
4                                                      1         
...                                                  ...         
37504                                                  2         
37505                                                  2         
37506                                                  2         
37507                                                  2         
37508                                                  2         

       Sediment Type - Exposure level  \
0                                 4.0   
1                                 2.0   
2                                 4.0   
3                                 2.0   
4                                 2.0   
...                               ...   
37504                             4.0   
37505                             4.0   
37506                   

In [91]:
#Classifying  Risk levels based in 20%, 40%, 60%, and 80& percentiles


RL1 = np.percentile(gornitz_ESL_filled["Risk Level"].dropna(), 20)
RL2 = np.percentile(gornitz_ESL_filled["Risk Level"].dropna(), 40)
RL3 = np.percentile(gornitz_ESL_filled["Risk Level"].dropna(), 60)
RL4 = np.percentile(gornitz_ESL_filled["Risk Level"].dropna(), 80)


gornitz_ESL_filled.loc[gornitz_ESL_filled["Risk Level"] <= RL1, "Risk Level Class"] = 1
gornitz_ESL_filled.loc[(gornitz_ESL_filled["Risk Level"] > RL1) & (gornitz_ESL_filled["Risk Level"] <= RL2), "Risk Level Class"] = 2
gornitz_ESL_filled.loc[(gornitz_ESL_filled["Risk Level"] > RL2) & (gornitz_ESL_filled["Risk Level"] <= RL3), "Risk Level Class"] = 3
gornitz_ESL_filled.loc[(gornitz_ESL_filled["Risk Level"] > RL3) & (gornitz_ESL_filled["Risk Level"] <= RL4), "Risk Level Class"] = 4
gornitz_ESL_filled.loc[gornitz_ESL_filled["Risk Level"] > RL4, "Risk Level Class"] = 5

gornitz_ESL_filled

transect_id  Shoreline_Change_Rate_PC - Hazard level  \
0       BOX_116_353_2                                      5.0   
1       BOX_116_353_3                                      2.0   
2       BOX_116_353_4                                      1.0   
3       BOX_116_353_5                                      2.0   
4       BOX_116_353_6                                      2.0   
...               ...                                      ...   
37504  BOX_139_002_61                                      2.0   
37505  BOX_139_002_62                                      2.0   
37506  BOX_139_002_63                                      2.0   
37507  BOX_139_002_64                                      2.0   
37508  BOX_139_002_65                                      2.0   

       Percentage of Built Up Area - Exposure level  \
0                                                 1   
1                                                 1   
2                                                 1   
3                                                 1   
4                                                 1   
...                                             ...   
37504                                             1   
37505                                             1   
37506                                             1   
37507                                             1   
37508                                             1   

       LECZ Area÷LECZ mean elevation - Exposure level  \
0                                                   2   
1                                                   3   
2                                                   4   
3                                                   4   
4                                                   5   
...                                               ...   
37504                                               2   
37505                                               2   
37506                                               3   
37507                                               3   
37508                                               3   

       Neashore Slope (tanβ or m^-1) - Exposure level  \
0                                                 4.0   
1                                                 4.0   
2                                                 4.0   
3                                                 4.0   
4                                                 4.0   
...                                               ...   
37504                                             3.0   
37505                                             3.0   
37506                                             3.0   
37507                                             3.0   
37508                                             3.0   

       Population Within 1km of the coastline - Exposure level  \
0                                                      1         
1                                                      1         
2                                                      1         
3                                                      1         
4                                                      1         
...                                                  ...         
37504                                                  2         
37505                                                  2         
37506                                                  2         
37507                                                  2         
37508                                                  2         

       Sediment Type - Exposure level  \
0                                 4.0   
1                                 2.0   
2                                 4.0   
3                                 2.0   
4                                 2.0   
...                               ...   
37504                             4.0   
37505                             4.0   
37506                   

In [92]:


df = gornitz_ESL.iloc[:,1:]

# Identify columns with NaN values
nan_columns = df.columns[df.isna().any()].tolist()

# Create a new column 'NaN_Columns' containing list of column names with NaN values for each row
gornitz_ESL_filled['Uncertainty_Columns'] = df.apply(lambda row: [col for col in nan_columns if pd.isna(row[col])], axis=1)
gornitz_ESL_filled['Uncertainty_Columns_length'] = gornitz_ESL_filled['Uncertainty_Columns'].apply(len)

df


Shoreline_Change_Rate_PC - Hazard level  \
0                                          5.0   
1                                          2.0   
2                                          1.0   
3                                          2.0   
4                                          2.0   
...                                        ...   
37504                                      2.0   
37505                                      2.0   
37506                                      2.0   
37507                                      2.0   
37508                                      2.0   

       Percentage of Built Up Area - Exposure level  \
0                                                 1   
1                                                 1   
2                                                 1   
3                                                 1   
4                                                 1   
...                                             ...   
37504                                             1   
37505                                             1   
37506                                             1   
37507                                             1   
37508                                             1   

       LECZ Area÷LECZ mean elevation - Exposure level  \
0                                                   2   
1                                                   3   
2                                                   4   
3                                                   4   
4                                                   5   
...                                               ...   
37504                                               2   
37505                                               2   
37506                                               3   
37507                                               3   
37508                                               3   

       Neashore Slope (tanβ or m^-1) - Exposure level  \
0                                                 4.0   
1                                                 4.0   
2                                                 4.0   
3                                                 4.0   
4                                                 4.0   
...                                               ...   
37504                                             3.0   
37505                                             3.0   
37506                                             3.0   
37507                                             3.0   
37508                                             3.0   

       Population Within 1km of the coastline - Exposure level  \
0                                                      1         
1                                                      1         
2                                                      1         
3                                                      1         
4                                                      1         
...                                                  ...         
37504                                                  2         
37505                                                  2         
37506                                                  2         
37507                                                  2         
37508                                                  2         

       Sediment Type - Exposure level  \
0                                 4.0   
1                                 2.0   
2                                 4.0   
3                                 2.0   
4                                 2.0   
...                               ...   
37504                             4.0   
37505                             4.0   
37506                             4.0   
37507                             4.0   
37508                             4.0   

       Infant Mortality Rate (3_yr_Average) - Vulnerability level  \
0                   

In [93]:

gornitz_ESL_filled["Confindence %"]=100*(indicator_num-gornitz_ESL_filled['Uncertainty_Columns'].apply(len))/indicator_num
gornitz_ESL_filled

transect_id  Shoreline_Change_Rate_PC - Hazard level  \
0       BOX_116_353_2                                      5.0   
1       BOX_116_353_3                                      2.0   
2       BOX_116_353_4                                      1.0   
3       BOX_116_353_5                                      2.0   
4       BOX_116_353_6                                      2.0   
...               ...                                      ...   
37504  BOX_139_002_61                                      2.0   
37505  BOX_139_002_62                                      2.0   
37506  BOX_139_002_63                                      2.0   
37507  BOX_139_002_64                                      2.0   
37508  BOX_139_002_65                                      2.0   

       Percentage of Built Up Area - Exposure level  \
0                                                 1   
1                                                 1   
2                                                 1   
3                                                 1   
4                                                 1   
...                                             ...   
37504                                             1   
37505                                             1   
37506                                             1   
37507                                             1   
37508                                             1   

       LECZ Area÷LECZ mean elevation - Exposure level  \
0                                                   2   
1                                                   3   
2                                                   4   
3                                                   4   
4                                                   5   
...                                               ...   
37504                                               2   
37505                                               2   
37506                                               3   
37507                                               3   
37508                                               3   

       Neashore Slope (tanβ or m^-1) - Exposure level  \
0                                                 4.0   
1                                                 4.0   
2                                                 4.0   
3                                                 4.0   
4                                                 4.0   
...                                               ...   
37504                                             3.0   
37505                                             3.0   
37506                                             3.0   
37507                                             3.0   
37508                                             3.0   

       Population Within 1km of the coastline - Exposure level  \
0                                                      1         
1                                                      1         
2                                                      1         
3                                                      1         
4                                                      1         
...                                                  ...         
37504                                                  2         
37505                                                  2         
37506                                                  2         
37507                                                  2         
37508                                                  2         

       Sediment Type - Exposure level  \
0                                 4.0   
1                                 2.0   
2                                 4.0   
3                                 2.0   
4                                 2.0   
...                               ...   
37504                             4.0   
37505                             4.0   
37506                   

In [94]:
# Read the CSV file into a DataFrame
circle_center_df = Exposure_df


# Identify the correct geometry column (replace 'geometry_column_name' with the actual column name)
geometry_column_name = 'geometry'
circle_center_df['x'] = circle_center_df[geometry_column_name].apply(lambda point_str: float(point_str.strip('POINT ()').split()[0]))
circle_center_df['y'] = circle_center_df[geometry_column_name].apply(lambda point_str: float(point_str.strip('POINT ()').split()[1]))

circle_center_df = circle_center_df.drop(columns=[geometry_column_name])

# Create the GeoDataFrame with the correct geometry column
gornitz_ESL_filled_gdf = gpd.GeoDataFrame(gornitz_ESL_filled, geometry=gpd.points_from_xy(circle_center_df.x, circle_center_df.y))



gornitz_ESL_filled_gdf

transect_id  Shoreline_Change_Rate_PC - Hazard level  \
0       BOX_116_353_2                                      5.0   
1       BOX_116_353_3                                      2.0   
2       BOX_116_353_4                                      1.0   
3       BOX_116_353_5                                      2.0   
4       BOX_116_353_6                                      2.0   
...               ...                                      ...   
37504  BOX_139_002_61                                      2.0   
37505  BOX_139_002_62                                      2.0   
37506  BOX_139_002_63                                      2.0   
37507  BOX_139_002_64                                      2.0   
37508  BOX_139_002_65                                      2.0   

       Percentage of Built Up Area - Exposure level  \
0                                                 1   
1                                                 1   
2                                                 1   
3                                                 1   
4                                                 1   
...                                             ...   
37504                                             1   
37505                                             1   
37506                                             1   
37507                                             1   
37508                                             1   

       LECZ Area÷LECZ mean elevation - Exposure level  \
0                                                   2   
1                                                   3   
2                                                   4   
3                                                   4   
4                                                   5   
...                                               ...   
37504                                               2   
37505                                               2   
37506                                               3   
37507                                               3   
37508                                               3   

       Neashore Slope (tanβ or m^-1) - Exposure level  \
0                                                 4.0   
1                                                 4.0   
2                                                 4.0   
3                                                 4.0   
4                                                 4.0   
...                                               ...   
37504                                             3.0   
37505                                             3.0   
37506                                             3.0   
37507                                             3.0   
37508                                             3.0   

       Population Within 1km of the coastline - Exposure level  \
0                                                      1         
1                                                      1         
2                                                      1         
3                                                      1         
4                                                      1         
...                                                  ...         
37504                                                  2         
37505                                                  2         
37506                                                  2         
37507                                                  2         
37508                                                  2         

       Sediment Type - Exposure level  \
0                                 4.0   
1                                 2.0   
2                                 4.0   
3                                 2.0   
4                                 2.0   
...                               ...   
37504                             4.0   
37505                             4.0   
37506                   

In [95]:
# import os
# from dotenv import load_dotenv

# # Load the .env file
# load_dotenv(r'C:\Users\rowe\Documents\GitHub\coclicodata\.env')

# # Access the Mapbox Access Token
# mapbox_access_token = os.getenv('MAPBOX_ACCESS_TOKEN')

# print("Mapbox Access Token:", mapbox_access_token)

In [96]:
img_lat = 18.1
img_lon = -77.3
view_width = 10

In [97]:
if Discrete_Risk_Bins:

    long_name="Risk Level Class"
    # color_scale = ['#33f510','#3CB371','#FFFF00', '#FFA500','#FF4500']
    label_dict = {
    1: "Very Low",
    2: "Low",
    3: "Medium",
    4: "High",
    5: "Very High"}

    colors = {'Very Low': '#33f510', 'Low': '#3CB371', 'Medium': '#FFFF00', 'High': '#FFA500', 'Very High': '#FF4500'}

    gornitz_ESL_filled_gdf[Value_to_show] = Haz_Component

    #Sorted for Risk level view
    sorted_CCN=gornitz_ESL_filled_gdf.sort_values(long_name)


    # Create scatter map plot
    fig_region = px.scatter_mapbox(sorted_CCN,
                            lat=sorted_CCN["geometry"].y,
                            lon=sorted_CCN["geometry"].x,
                            # hover_name=sorted_CCN[long_name].replace(label_dict),
                            hover_name=Value_to_show,
                            color=sorted_CCN[long_name].replace(label_dict),
                            # color=sorted_CCN[long_name],
                            color_discrete_map=colors,
                            mapbox_style="carto-positron",width=2000,
                            height=1200)


    # Update map layout to adjust center and zoom
    fig_region.update_layout(mapbox=dict(center=dict(lat=img_lat + 1, lon=img_lon + 4), zoom=5.5),
                    title=f"{gornitz_ESL_filled_gdf.columns[1].replace('Hazard', 'Risk')}{var} Discrete Distribution along Caribbean's shoreline")

    fig_region .update_layout(legend=dict(
    traceorder='normal',
    title=long_name,
    title_font=dict(size=16),
    itemsizing='constant',))
    fig_region.show()


    fig_name_shoreline=gornitz_ESL_filled_gdf.columns[1].replace('Hazard', 'Risk') +var+"Discrete- Caribbean.png"
    pio.write_image(fig_region, os.path.join(img_directory_path, fig_name_shoreline))

In [98]:

if not Discrete_Risk_Bins or Both_Plots:

    long_name = "Risk Level"
    # Define tick names
    tick_names = ["Very Low", "Low", "Moderate", "High", "Very High"]

    tk1=np.min(gornitz_ESL_filled_gdf[long_name].dropna())
    tk5=np.max(gornitz_ESL_filled_gdf[long_name].dropna())
    tk3=np.mean([tk1,tk5])
    tk4=np.mean([tk3,tk5])
    tk2=np.mean([tk3,tk1])

    
    tick_vals= [tk1, tk2,tk3, tk4, tk5]
   

    # Define parameters

    color_scale = ['#33f510', '#3CB371', '#FFFF00', '#FFA500', '#FF4500']

    # Update Hazard Component values
    gornitz_ESL_filled_gdf[Value_to_show] = Haz_Component

    # Sort values for Risk level view
    sorted_CCN = gornitz_ESL_filled_gdf.sort_values(long_name)

    # Create scatter map plot
    fig_region = px.scatter_mapbox(sorted_CCN,
                                    lat=sorted_CCN["geometry"].y,
                                    lon=sorted_CCN["geometry"].x,
                                    hover_name=Value_to_show,
                                    color=sorted_CCN[long_name],
                                    color_continuous_scale=color_scale,
                                    mapbox_style="carto-positron",
                                    width=2000,
                                    height=1200)

    # Update the tick labels
    fig_region.update_layout(coloraxis_colorbar=dict(title=long_name, tickvals=tick_vals, ticktext=tick_names, tickfont=dict(size=15, color='black')))

    # Update map layout to adjust center and zoom
    fig_region.update_layout(mapbox=dict(center=dict(lat=img_lat + 1, lon=img_lon + 4), zoom=5.5),
                            title=f"{gornitz_ESL_filled_gdf.columns[1].replace('Hazard', 'Risk')}{var} Continuous Distribution along Caribbean's shoreline")

    # Show the figure
    fig_region.show()

    # Save the figure
    fig_name_shoreline = gornitz_ESL_filled_gdf.columns[1].replace('Hazard', 'Risk') + var + "Continuous- Caribbean.png"
    pio.write_image(fig_region, os.path.join(img_directory_path, fig_name_shoreline))


In [99]:
gornitz_ESL_filled_gdf

transect_id  Shoreline_Change_Rate_PC - Hazard level  \
0       BOX_116_353_2                                      5.0   
1       BOX_116_353_3                                      2.0   
2       BOX_116_353_4                                      1.0   
3       BOX_116_353_5                                      2.0   
4       BOX_116_353_6                                      2.0   
...               ...                                      ...   
37504  BOX_139_002_61                                      2.0   
37505  BOX_139_002_62                                      2.0   
37506  BOX_139_002_63                                      2.0   
37507  BOX_139_002_64                                      2.0   
37508  BOX_139_002_65                                      2.0   

       Percentage of Built Up Area - Exposure level  \
0                                                 1   
1                                                 1   
2                                                 1   
3                                                 1   
4                                                 1   
...                                             ...   
37504                                             1   
37505                                             1   
37506                                             1   
37507                                             1   
37508                                             1   

       LECZ Area÷LECZ mean elevation - Exposure level  \
0                                                   2   
1                                                   3   
2                                                   4   
3                                                   4   
4                                                   5   
...                                               ...   
37504                                               2   
37505                                               2   
37506                                               3   
37507                                               3   
37508                                               3   

       Neashore Slope (tanβ or m^-1) - Exposure level  \
0                                                 4.0   
1                                                 4.0   
2                                                 4.0   
3                                                 4.0   
4                                                 4.0   
...                                               ...   
37504                                             3.0   
37505                                             3.0   
37506                                             3.0   
37507                                             3.0   
37508                                             3.0   

       Population Within 1km of the coastline - Exposure level  \
0                                                      1         
1                                                      1         
2                                                      1         
3                                                      1         
4                                                      1         
...                                                  ...         
37504                                                  2         
37505                                                  2         
37506                                                  2         
37507                                                  2         
37508                                                  2         

       Sediment Type - Exposure level  \
0                                 4.0   
1                                 2.0   
2                                 4.0   
3                                 2.0   
4                                 2.0   
...                               ...   
37504                             4.0   
37505                             4.0   
37506                   

In [100]:
gornitz_ESL_filled_gdf.to_csv(save_directory+f"/{gornitz_ESL_filled_gdf.columns[1].replace('Hazard', 'Risk')}.csv",index=False)

Curacao Multi-Criteria Risk Level for Extreme Sea Level Hazard Using Mclaughlin and Cooper (2010)